# Human numbers

In [310]:
from fastai.text import *
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [313]:
bs=64

## Data

In [314]:
path = untar_data(URLs.HUMAN_NUMBERS)
path.ls()

[PosixPath('/projects/da_workspace/szspace/.fastai/data/human_numbers/valid.txt'),
 PosixPath('/projects/da_workspace/szspace/.fastai/data/human_numbers/train.txt')]

In [315]:
def readnums(d): return [', '.join(o.strip() for o in open(path/d).readlines())]

In [316]:
train_txt = readnums('train.txt'); train_txt[0][:80]

'one, two, three, four, five, six, seven, eight, nine, ten, eleven, twelve, thirt'

In [317]:
train_txt[0][:200]

'one, two, three, four, five, six, seven, eight, nine, ten, eleven, twelve, thirteen, fourteen, fifteen, sixteen, seventeen, eighteen, nineteen, twenty, twenty one, twenty two, twenty three, twenty fou'

In [318]:
valid_txt = readnums('valid.txt'); valid_txt[0][-80:]

' nine thousand nine hundred ninety eight, nine thousand nine hundred ninety nine'

In [319]:
train = TextList(train_txt, path=path)
valid = TextList(valid_txt, path=path)

src = ItemLists(path=path, train=train, valid=valid).label_for_lm()
data = src.databunch(bs=bs)

In [320]:
train[0].text[:80]

'xxbos one , two , three , four , five , six , seven , eight , nine , ten , eleve'

language model databunch, TextLMDataBuch, it has train dataloader and valid dataloader. batch size is 64 here. split the entire text document into 64 pieces with roughly equal size. train data set (LMTextList, LMLabelList) is english numbers from one to seven thousand nine hundred ninty nine. data.train_ds.y onlys shows LMLabelList. it is actually the numbers that are offset by one.

In [321]:
data.train_ds.y

LMLabelList (1 items)

Path: /projects/da_workspace/szspace/.fastai/data/human_numbers

In [322]:
data.valid_ds[0][0]

Text xxbos eight thousand one , eight thousand two , eight thousand three , eight thousand four , eight thousand five , eight thousand six , eight thousand seven , eight thousand eight , eight thousand nine , eight thousand ten , eight thousand eleven , eight thousand twelve , eight thousand thirteen , eight thousand fourteen , eight thousand fifteen , eight thousand sixteen , eight thousand seventeen , eight thousand eighteen , eight thousand nineteen , eight thousand twenty , eight thousand twenty one , eight thousand twenty two , eight thousand twenty three , eight thousand twenty four , eight thousand twenty five , eight thousand twenty six , eight thousand twenty seven , eight thousand twenty eight , eight thousand twenty nine , eight thousand thirty , eight thousand thirty one , eight thousand thirty two , eight thousand thirty three , eight thousand thirty four , eight thousand thirty five , eight thousand thirty six , eight thousand thirty seven , eight thousand thirty eight , 

In [323]:
data.valid_ds[0][0].data[:30] # shows the code
np.unique(data.valid_ds[0][0].data)

array([ 2, 19, 11, 12,  9, 19, 11, 13,  9, 19, 11, 14,  9, 19, 11, 15,  9, 19, 11, 16,  9, 19, 11, 17,  9, 19, 11, 18,
        9, 19])

array([ 2,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35,
       36, 37, 38])

In [324]:
data.valid_ds.vocab.numericalize(['one', 'two', 'three','eight', 'thousand', 'twenty', 'eight'])

[12, 13, 14, 19, 11, 21, 19]

In [325]:
data.valid_ds.vocab.textify(data.valid_ds[0][0].data[:30])

'xxbos eight thousand one , eight thousand two , eight thousand three , eight thousand four , eight thousand five , eight thousand six , eight thousand seven , eight'

In [326]:
len(data.valid_ds[0][0].data) 
# this is the number of tokens in the text, split by space and count
# token is each word split by space, for example twenty one will be 2 tokens: twenty and one, 
# , is also a token and other thing like start of the string xxbos

13017

In [327]:
len(data.valid_ds[0][0].data)

13017

In [329]:
data.bptt # default for back propagate through time (sequence input length) is 70 
len(data.valid_dl) # number of batches

70

3

In [330]:
data.bptt, len(data.valid_dl)

(70, 3)

there are 13017 tokens in the valid text, divided by batch size 64, this is the number of tokens in each batch, th
en divided by the bptt sequence length, this is how many times it takes to iterate the data loader.

In [331]:
13017/70/bs

2.905580357142857

In [332]:
it = iter(data.valid_dl)
x1,y1 = next(it)
x2,y2 = next(it)
x3,y3 = next(it)
it.close()

In [333]:
x1.numel()+x2.numel()+x3.numel()

13440

In [335]:
x1.shape,y1.shape
x3.shape,y3.shape

(torch.Size([64, 70]), torch.Size([64, 70]))

(torch.Size([64, 70]), torch.Size([64, 70]))

you can see batch x1 and x2 join up.[ 2, 19, 11,  ..., 36,  9, 19] followed by [11, 37,  9,  ..., 22, 13,  9]. also for y1, [19, 11, 12,  ...,  9, 19, 11], after 9, 19, the next word should be 11. and then 37. so the input is bs * bptt, in this case is 64*70.

In [336]:
x1
x2

tensor([[ 2, 19, 11,  ..., 36,  9, 19],
        [ 9, 19, 11,  ..., 24, 20,  9],
        [11, 27, 18,  ...,  9, 19, 11],
        ...,
        [20, 11, 20,  ..., 11, 20, 10],
        [20, 11, 20,  ..., 24,  9, 20],
        [20, 10, 26,  ..., 20, 11, 20]], device='cuda:0')

tensor([[11, 37,  9,  ..., 22, 13,  9],
        [19, 11, 25,  ...,  9, 19, 11],
        [12, 10, 12,  ..., 10, 31,  9],
        ...,
        [21, 12,  9,  ..., 20, 10, 22],
        [11, 20, 10,  ...,  9, 20, 11],
        [10, 27,  9,  ..., 11, 20, 10]], device='cuda:0')

In [337]:
y1
y2

tensor([[19, 11, 12,  ...,  9, 19, 11],
        [19, 11, 23,  ..., 20,  9, 19],
        [27, 18,  9,  ..., 19, 11, 12],
        ...,
        [11, 20, 10,  ..., 20, 10, 21],
        [11, 20, 10,  ...,  9, 20, 11],
        [10, 26,  9,  ..., 11, 20, 10]], device='cuda:0')

tensor([[37,  9, 19,  ..., 13,  9, 19],
        [11, 25,  9,  ..., 19, 11, 26],
        [10, 12,  9,  ..., 31,  9, 19],
        ...,
        [12,  9, 20,  ..., 10, 22, 12],
        [20, 10, 24,  ..., 20, 11, 20],
        [27,  9, 20,  ..., 20, 10, 28]], device='cuda:0')

In [338]:
x1[:,0] # not sure why we look at the first word in batch 1 in each batch of the 64 batches
x1[:,0].numel()

tensor([ 2,  9, 11, 12, 13, 11, 10,  9, 10, 14, 19, 25, 19, 15, 16, 11, 19,  9,
        10,  9, 19, 25, 19, 11, 19, 11, 10,  9, 19, 20, 11, 26, 20, 23, 20, 20,
        24, 20, 11, 14, 11, 11,  9, 14,  9, 20, 10, 20, 35, 17, 11, 10,  9, 17,
         9, 20, 10, 20, 11, 20, 11, 20, 20, 20], device='cuda:0')

64

In [339]:
x1[0,:].numel()

70

In [340]:
y1[:,0]

tensor([19, 19, 27, 10,  9, 12, 32, 19, 26, 10, 11, 15, 11, 10,  9, 15, 11, 19,
        26, 19, 11, 18, 11, 18,  9, 18, 21, 19, 10, 10, 20,  9, 11, 16, 11, 11,
        13, 11, 13,  9, 13, 14, 20, 10, 20, 11, 24, 11,  9,  9, 16, 17, 20, 10,
        20, 11, 24, 11, 19,  9, 19, 11, 11, 10], device='cuda:0')

In [341]:
v = data.valid_ds.vocab

In [345]:
v.textify(x1[0])
v.textify(x1[63])

'xxbos eight thousand one , eight thousand two , eight thousand three , eight thousand four , eight thousand five , eight thousand six , eight thousand seven , eight thousand eight , eight thousand nine , eight thousand ten , eight thousand eleven , eight thousand twelve , eight thousand thirteen , eight thousand fourteen , eight thousand fifteen , eight thousand sixteen , eight thousand seventeen , eight'

'nine hundred seventy , nine thousand nine hundred seventy one , nine thousand nine hundred seventy two , nine thousand nine hundred seventy three , nine thousand nine hundred seventy four , nine thousand nine hundred seventy five , nine thousand nine hundred seventy six , nine thousand nine hundred seventy seven , nine thousand nine hundred seventy eight , nine thousand nine hundred seventy nine , nine thousand nine'

In [346]:
v.textify(y1[0])
v.textify(y1[63])

'eight thousand one , eight thousand two , eight thousand three , eight thousand four , eight thousand five , eight thousand six , eight thousand seven , eight thousand eight , eight thousand nine , eight thousand ten , eight thousand eleven , eight thousand twelve , eight thousand thirteen , eight thousand fourteen , eight thousand fifteen , eight thousand sixteen , eight thousand seventeen , eight thousand'

'hundred seventy , nine thousand nine hundred seventy one , nine thousand nine hundred seventy two , nine thousand nine hundred seventy three , nine thousand nine hundred seventy four , nine thousand nine hundred seventy five , nine thousand nine hundred seventy six , nine thousand nine hundred seventy seven , nine thousand nine hundred seventy eight , nine thousand nine hundred seventy nine , nine thousand nine hundred'

In [347]:
v.textify(x2[0])

'thousand eighteen , eight thousand nineteen , eight thousand twenty , eight thousand twenty one , eight thousand twenty two , eight thousand twenty three , eight thousand twenty four , eight thousand twenty five , eight thousand twenty six , eight thousand twenty seven , eight thousand twenty eight , eight thousand twenty nine , eight thousand thirty , eight thousand thirty one , eight thousand thirty two ,'

In [348]:
v.textify(x3[0])

'eight thousand thirty three , eight thousand thirty four , eight thousand thirty five , eight thousand thirty six , eight thousand thirty seven , eight thousand thirty eight , eight thousand thirty nine , eight thousand forty , eight thousand forty one , eight thousand forty two , eight thousand forty three , eight thousand forty four , eight thousand forty five , eight thousand forty six , eight'

In [349]:
v.textify(x1[1])

', eight thousand forty six , eight thousand forty seven , eight thousand forty eight , eight thousand forty nine , eight thousand fifty , eight thousand fifty one , eight thousand fifty two , eight thousand fifty three , eight thousand fifty four , eight thousand fifty five , eight thousand fifty six , eight thousand fifty seven , eight thousand fifty eight , eight thousand fifty nine ,'

In [350]:
v.textify(x2[1])

'eight thousand sixty , eight thousand sixty one , eight thousand sixty two , eight thousand sixty three , eight thousand sixty four , eight thousand sixty five , eight thousand sixty six , eight thousand sixty seven , eight thousand sixty eight , eight thousand sixty nine , eight thousand seventy , eight thousand seventy one , eight thousand seventy two , eight thousand seventy three , eight thousand'

In [351]:
v.textify(x3[1])

'seventy four , eight thousand seventy five , eight thousand seventy six , eight thousand seventy seven , eight thousand seventy eight , eight thousand seventy nine , eight thousand eighty , eight thousand eighty one , eight thousand eighty two , eight thousand eighty three , eight thousand eighty four , eight thousand eighty five , eight thousand eighty six , eight thousand eighty seven , eight thousand eighty'

In [352]:
v.textify(x3[-1])

'ninety , nine thousand nine hundred ninety one , nine thousand nine hundred ninety two , nine thousand nine hundred ninety three , nine thousand nine hundred ninety four , nine thousand nine hundred ninety five , nine thousand nine hundred ninety six , nine thousand nine hundred ninety seven , nine thousand nine hundred ninety eight , nine thousand nine hundred ninety nine xxbos eight thousand one , eight'

In [353]:
data.show_batch(ds_type=DatasetType.Valid)

## Single fully connected model

In [354]:
data = src.databunch(bs=bs, bptt=3)

In [355]:
it = iter(data.valid_dl)
x1,y1 = next(it)
x2,y2 = next(it)
x3,y3 = next(it)
it.close()

In [359]:
x1.shape

torch.Size([64, 3])

In [363]:
v.textify(x1[0])
v.textify(x1[1])
v.textify(y1[0])
v.textify(y1[1])

'xxbos eight thousand'

', eight thousand'

'eight thousand one'

'eight thousand forty'

In [364]:
x,y = data.one_batch()
x.shape,y.shape

(torch.Size([64, 3]), torch.Size([64, 3]))

In [79]:
# v is the vocab

In [369]:
v.itos[:10]
v.stoi # this is the vocab dictionary

['xxunk',
 'xxpad',
 'xxbos',
 'xxeos',
 'xxfld',
 'xxmaj',
 'xxup',
 'xxrep',
 'xxwrep',
 ',']

defaultdict(int,
            {'xxunk': 0,
             'xxpad': 1,
             'xxbos': 2,
             'xxeos': 3,
             'xxfld': 4,
             'xxmaj': 5,
             'xxup': 6,
             'xxrep': 7,
             'xxwrep': 8,
             ',': 9,
             'hundred': 10,
             'thousand': 11,
             'one': 12,
             'two': 13,
             'three': 14,
             'four': 15,
             'five': 16,
             'six': 17,
             'seven': 18,
             'eight': 19,
             'nine': 20,
             'twenty': 21,
             'thirty': 22,
             'forty': 23,
             'fifty': 24,
             'sixty': 25,
             'seventy': 26,
             'eighty': 27,
             'ninety': 28,
             'ten': 29,
             'eleven': 30,
             'twelve': 31,
             'thirteen': 32,
             'fourteen': 33,
             'fifteen': 34,
             'sixteen': 35,
             'seventeen': 36,
             'eight

In [370]:
nv = len(v.itos); nv

40

In [372]:
x[:4]; y[:4]

tensor([[13,  9, 14],
        [13, 10, 30],
        [10, 26, 17],
        [ 9, 16, 10]])

tensor([[ 9, 14,  9],
        [10, 30,  9],
        [26, 17,  9],
        [16, 10, 23]])

In [374]:
nh = 65
# nh=10

In [375]:
def loss4(input,target): return F.cross_entropy(input, target[:,-1])
def acc4 (input,target): return accuracy(input, target[:,-1])

In [381]:
class Model0(nn.Module):
    def __init__(self):
        super().__init__()
        self.i_h = nn.Embedding(nv,nh)  # green arrow
        self.h_h = nn.Linear(nh,nh)     # brown arrow
        self.h_o = nn.Linear(nh,nv)     # blue arrow
        self.bn = nn.BatchNorm1d(nh)
        
    def forward(self, x):
        print('xshape', x.shape)
        h = self.bn(F.relu(self.h_h(self.i_h(x[:,0]))))
        print('hidden shape', h.shape)
        if x.shape[1]>1:
            h = h + self.i_h(x[:,1])
            h = self.bn(F.relu(self.h_h(h)))
            print('2nd hidden shape', h.shape)
        if x.shape[1]>2:
            h = h + self.i_h(x[:,2])
            h = self.bn(F.relu(self.h_h(h)))
            print('3rd hidden shape', h.shape)
#         print(x.shape, h.shape, self.h_o(h).shape)
        # is the input and output supposed to offset by one???
        print('output shape', self.h_o(h).shape)
        return self.h_o(h)

In [382]:
learn = Learner(data, Model0(), loss_func=loss4, metrics=acc4)

In [383]:
learn.summary()

xshape torch.Size([1, 3])
hidden shape torch.Size([1, 65])
2nd hidden shape torch.Size([1, 65])
3rd hidden shape torch.Size([1, 65])
output shape torch.Size([1, 40])


Model0
Layer (type)         Output Shape         Param #    Trainable 
Embedding            [65]                 2,600      True      
______________________________________________________________________
Linear               [65]                 4,290      True      
______________________________________________________________________
Linear               [40]                 2,640      True      
______________________________________________________________________
BatchNorm1d          [65]                 130        True      
______________________________________________________________________

Total params: 9,660
Total trainable params: 9,660
Total non-trainable params: 0
Optimized with 'torch.optim.adam.Adam', betas=(0.9, 0.99)
Using true weight decay as discussed in https://www.fast.ai/2018/07/02/adam-weight-decay/ 
Loss function : function
Callbacks functions applied 

In [384]:
# learn.fit_one_cycle(6, 1e-4)
learn.fit_one_cycle(1, 1e-4)

xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output s

xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output s

hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
x

2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden s

output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden s

xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output s

xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output shape torch.Size([64, 40])
xshape torch.Size([64, 3])
hidden shape torch.Size([64, 65])
2nd hidden shape torch.Size([64, 65])
3rd hidden shape torch.Size([64, 65])
output s

In [385]:
# it is like one batch x (64*3, one mini batch has 64 3 words sequences) goes in,
# the NN take in the first word from each of the 64 sequence, look up its embedding from the 
# 40*65 matrix gives a 64*65(nh) activation. this is added to the next word's 64*65(nh). and then
# go through a linear and RELU gives another 64*65(nh) activation (h_to_h).
# finally spits out 64*40 tells probability of the each of the 40 word in the vocab.
# real RNN predict every single 2 to n+1 word. the same length as input sequence. every loop predict the next word


# activation shapes
# x shape torch.Size([64, 3])
# hidden shape torch.Size([64, 65])
# 2nd hidden shape torch.Size([64, 65])
# 3rd hidden shape torch.Size([64, 65])
# output shape torch.Size([64, 40])


# parameter shapes
# torch.Size([40, 65])
# torch.Size([65, 65])
# torch.Size([65])
# torch.Size([40, 65])
# torch.Size([40])
# torch.Size([65])
# torch.Size([65])

In [380]:
for p in list(learn.model.parameters()):
    print(p.shape)

torch.Size([40, 65])
torch.Size([65, 65])
torch.Size([65])
torch.Size([40, 65])
torch.Size([40])
torch.Size([65])
torch.Size([65])


## Same thing with a loop

In [ ]:
class Model1(nn.Module):
    def __init__(self):
        super().__init__()
        self.i_h = nn.Embedding(nv,nh)  # green arrow
        self.h_h = nn.Linear(nh,nh)     # brown arrow
        self.h_o = nn.Linear(nh,nv)     # blue arrow
        self.bn = nn.BatchNorm1d(nh)
        
    def forward(self, x):
        h = torch.zeros(x.shape[0], nh).to(device=x.device)
        for i in range(x.shape[1]):
            h = h + self.i_h(x[:,i])
            h = self.bn(F.relu(self.h_h(h)))
        return self.h_o(h)

In [ ]:
learn = Learner(data, Model1(), loss_func=loss4, metrics=acc4)

In [ ]:
learn.fit_one_cycle(6, 1e-4)

## Multi fully connected model

In [ ]:
data = src.databunch(bs=bs, bptt=20)

In [ ]:
x,y = data.one_batch()
x.shape,y.shape

(torch.Size([64, 20]), torch.Size([64, 20]))

In [87]:
class Model2(nn.Module):
    def __init__(self):
        super().__init__()
        self.i_h = nn.Embedding(nv,nh)
        self.h_h = nn.Linear(nh,nh)
        self.h_o = nn.Linear(nh,nv)
        self.bn = nn.BatchNorm1d(nh)
        
    def forward(self, x):
        print(x)
        h = torch.zeros(x.shape[0], nh).to(device=x.device)
        res = []
        for i in range(x.shape[1]):
            h = h + self.i_h(x[:,i])
            h = F.relu(self.h_h(h))
            res.append(self.h_o(self.bn(h)))
        return torch.stack(res, dim=1)

In [88]:
learn = Learner(data, Model2(), metrics=accuracy)

In [89]:
learn.fit_one_cycle(10, 1e-4, pct_start=0.1)

tensor([[ 2, 12,  9],
        [10, 29,  9],
        [16,  9, 14],
        [10, 23, 14],
        [10, 19,  9],
        [10, 26, 15],
        [12,  9, 12],
        [15,  9, 12],
        [ 9, 12, 11],
        [11, 15, 10],
        [ 9, 12, 11],
        [11, 17, 10],
        [11, 18, 10],
        [10, 26, 15],
        [10, 28,  9],
        [10, 22, 19],
        [24, 15,  9],
        [ 9, 13, 11],
        [ 9, 13, 11],
        [14,  9, 13],
        [13, 11, 18],
        [11, 19, 10],
        [20, 10, 24],
        [11, 28, 20],
        [14, 11, 13],
        [22, 15,  9],
        [24,  9, 14],
        [ 9, 14, 11],
        [14, 11, 17],
        [11, 18, 10],
        [36,  9, 14],
        [11, 23, 19],
        [12, 10, 26],
        [10, 28, 16],
        [10, 32,  9],
        [10, 22,  9],
        [17,  9, 15],
        [ 9, 15, 11],
        [15, 11, 19],
        [11, 20, 10],
        [11, 12, 10],
        [11, 13, 10],
        [10, 26, 16],
        [28, 12,  9],
        [16, 11, 17],
        [2

tensor([[ 9, 32,  9],
        [10, 35,  9],
        [27,  9, 14],
        [16, 10, 23],
        [10, 33,  9],
        [19, 10, 26],
        [23, 17,  9],
        [11, 12, 10],
        [13, 10, 28],
        [11, 15, 10],
        [16, 10, 21],
        [23, 16,  9],
        [12,  9, 12],
        [ 9, 12, 11],
        [12, 11, 20],
        [13, 11, 12],
        [13, 11, 13],
        [14, 10, 26],
        [15, 10, 28],
        [18,  9, 13],
        [10, 21, 16],
        [12,  9, 13],
        [18,  9, 13],
        [10, 14,  9],
        [ 9, 14, 11],
        [14, 11, 14],
        [11, 15, 10],
        [16, 10, 26],
        [10, 27, 17],
        [11, 19, 10],
        [21, 12,  9],
        [11, 24, 14],
        [ 9, 15, 11],
        [ 9, 15, 11],
        [10, 36,  9],
        [15, 11, 16],
        [11, 17, 10],
        [18, 10, 25],
        [27, 13,  9],
        [28, 19,  9],
        [23, 17,  9],
        [13,  9, 16],
        [ 9, 16, 11],
        [16, 11, 15],
        [16, 11, 17],
        [1

tensor([[16,  9, 21],
        [10, 21, 14],
        [17,  9, 14],
        [10, 24, 15],
        [12,  9, 18],
        [10, 27, 16],
        [13,  9, 12],
        [27, 13,  9],
        [28, 19,  9],
        [11, 15, 10],
        [14,  9, 12],
        [ 9, 12, 11],
        [12, 11, 18],
        [19, 10, 27],
        [20, 10, 28],
        [12, 10, 23],
        [10, 25, 13],
        [26, 19,  9],
        [15,  9, 13],
        [31,  9, 13],
        [20,  9, 13],
        [13, 11, 19],
        [11, 20, 10],
        [10, 19,  9],
        [11, 13, 10],
        [10, 23, 13],
        [10, 24, 19],
        [15,  9, 14],
        [ 9, 14, 11],
        [11, 19, 10],
        [ 9, 14, 11],
        [11, 24, 20],
        [11, 12, 10],
        [ 9, 15, 11],
        [15, 10, 21],
        [16, 10, 22],
        [24, 15,  9],
        [26,  9, 15],
        [ 9, 15, 11],
        [11, 16,  9],
        [16, 11, 12],
        [16, 11, 13],
        [14, 10, 27],
        [15, 10, 28],
        [16, 11, 17],
        [1

tensor([[ 9, 22, 14],
        [21, 18,  9],
        [14, 10, 28],
        [24, 19,  9],
        [ 9, 18, 10],
        [27, 20,  9],
        [ 9, 12, 11],
        [27, 16,  9],
        [12, 11, 14],
        [21,  9, 12],
        [17,  9, 12],
        [12, 11, 17],
        [12, 11, 18],
        [19, 10, 27],
        [13,  9, 13],
        [12, 10, 23],
        [10, 25, 16],
        [12,  9, 13],
        [18,  9, 13],
        [11, 17, 10],
        [ 9, 13, 11],
        [13, 11, 19],
        [11, 20, 10],
        [14, 11, 12],
        [11, 13, 10],
        [10, 23, 16],
        [25, 12,  9],
        [18,  9, 14],
        [ 9, 14, 11],
        [30,  9, 14],
        [ 9, 14, 11],
        [14,  9, 15],
        [11, 12, 10],
        [14, 10, 18],
        [15, 10, 21],
        [10, 23, 12],
        [24, 18,  9],
        [14,  9, 15],
        [ 9, 15, 11],
        [29,  9, 16],
        [16, 11, 12],
        [16, 11, 13],
        [14, 10, 27],
        [ 9, 16, 11],
        [10, 21, 12],
        [1

tensor([[23, 13,  9],
        [13, 10, 22],
        [28, 17,  9],
        [16, 10, 25],
        [22, 12,  9],
        [19, 10, 28],
        [25, 13,  9],
        [10, 27, 20],
        [10, 17,  9],
        [21, 15,  9],
        [23,  9, 12],
        [ 9, 12, 11],
        [12, 11, 18],
        [11, 19, 10],
        [11, 20,  9],
        [12, 10, 24],
        [13, 10, 25],
        [27, 16,  9],
        [13, 11, 16],
        [21,  9, 13],
        [17,  9, 13],
        [13, 11, 19],
        [13, 11, 20],
        [10, 35,  9],
        [11, 13, 10],
        [14, 10, 23],
        [10, 25, 16],
        [12,  9, 14],
        [18,  9, 14],
        [11, 19, 10],
        [ 9, 14, 11],
        [15, 11, 25],
        [11, 12, 10],
        [ 9, 15, 11],
        [11, 15, 10],
        [16, 10, 23],
        [25, 12,  9],
        [26, 18,  9],
        [ 9, 15, 11],
        [11, 36,  9],
        [ 9, 16, 11],
        [16, 11, 13],
        [11, 14, 10],
        [16, 10, 18],
        [17, 10, 21],
        [1

...

tensor([[ 9, 19, 11],
        [11, 26,  9],
        [20,  9, 19],
        [23,  9, 19],
        [19, 11, 12],
        [10, 28, 20],
        [ 9, 19, 11],
        [13, 10, 25],
        [ 9, 19, 11],
        [19, 11, 14],
        [10, 24, 13],
        [19, 11, 14],
        [11, 15, 10],
        [14,  9, 19],
        [11, 15, 10],
        [19, 11, 16],
        [ 9, 19, 11],
        [16, 10, 25],
        [ 9, 19, 11],
        [19, 11, 17],
        [10, 24, 16],
        [19, 11, 17],
        [35,  9, 19],
        [23, 17,  9],
        [11, 18, 10],
        [10, 17,  9],
        [ 9, 19, 11],
        [19, 10, 25],
        [17,  9, 19],
        [19, 11, 20],
        [10, 24, 19],
        [19, 11, 20],
        [21, 19,  9],
        [ 9, 20, 11],
        [10, 20,  9],
        [12, 10, 23],
        [ 9, 20, 11],
        [12, 10, 28],
        [22, 12,  9],
        [11, 13, 10],
        [10, 28,  9],
        [ 9, 20, 11],
        [14, 10, 24],
        [12,  9, 20],
        [20, 11, 15],
        [1

tensor([[13,  9, 19],
        [19, 11, 26],
        [31,  9, 19],
        [12, 10, 23],
        [13,  9, 19],
        [10, 13,  9],
        [10, 22, 15],
        [ 9, 19, 11],
        [10, 28, 14],
        [21, 16,  9],
        [19, 11, 14],
        [27, 15,  9],
        [11, 15, 10],
        [15, 10, 23],
        [16,  9, 19],
        [19, 11, 16],
        [10, 22, 18],
        [ 9, 19, 11],
        [10, 28, 17],
        [21, 19,  9],
        [19, 11, 17],
        [27, 18,  9],
        [38,  9, 19],
        [11, 18, 10],
        [19,  9, 19],
        [10, 20,  9],
        [10, 23,  9],
        [ 9, 19, 11],
        [19, 10, 28],
        [12,  9, 19],
        [11, 20, 10],
        [28,  9, 19],
        [11, 22, 13],
        [14,  9, 20],
        [10, 31,  9],
        [20, 11, 12],
        [26, 13,  9],
        [13, 10, 13],
        [11, 13, 10],
        [14,  9, 20],
        [11, 13, 10],
        [10, 21, 16],
        [ 9, 20, 11],
        [14, 10, 27],
        [20, 11, 15],
        [2

tensor([[11, 22, 17],
        [18,  9, 19],
        [34,  9, 19],
        [ 9, 19, 11],
        [12, 10, 26],
        [10, 16,  9],
        [19, 11, 13],
        [10, 25, 17],
        [19, 11, 13],
        [11, 14, 10],
        [24, 18,  9],
        [11, 14, 10],
        [11, 15, 10],
        [ 9, 19, 11],
        [15, 10, 26],
        [19, 11, 16],
        [19, 11, 16],
        [10, 25, 20],
        [19, 11, 16],
        [17, 10, 22],
        [25,  9, 19],
        [11, 17, 10],
        [10, 21, 13],
        [ 9, 19, 11],
        [10, 27, 12],
        [10, 31,  9],
        [11, 19, 10],
        [26, 13,  9],
        [20, 10, 13],
        [20, 10, 22],
        [14,  9, 19],
        [20, 10, 28],
        [ 9, 20, 11],
        [11, 26, 18],
        [10, 34,  9],
        [23, 16,  9],
        [11, 12, 10],
        [13, 10, 16],
        [17,  9, 20],
        [13, 10, 25],
        [16,  9, 20],
        [20, 11, 14],
        [10, 24, 18],
        [ 9, 20, 11],
        [20, 11, 15],
        [2

tensor([[ 9, 19, 11],
        [27, 12,  9],
        [37,  9, 19],
        [10, 23, 19],
        [ 9, 19, 11],
        [10, 19,  9],
        [22, 20,  9],
        [19, 11, 13],
        [28, 19,  9],
        [ 9, 19, 11],
        [11, 14, 10],
        [20,  9, 19],
        [19, 11, 15],
        [24, 12,  9],
        [19, 11, 15],
        [19, 11, 16],
        [13,  9, 19],
        [11, 16, 10],
        [19, 11, 17],
        [ 9, 19, 11],
        [17, 10, 25],
        [ 9, 19, 11],
        [19, 11, 18],
        [10, 24, 15],
        [19, 11, 18],
        [10, 34,  9],
        [16,  9, 19],
        [11, 19, 10],
        [20, 10, 16],
        [ 9, 19, 11],
        [20, 10, 25],
        [ 9, 19, 11],
        [22, 20,  9],
        [20, 11, 27],
        [10, 37,  9],
        [11, 12, 10],
        [18,  9, 20],
        [13, 10, 19],
        [13, 10, 22],
        [ 9, 20, 11],
        [13, 10, 28],
        [22,  9, 20],
        [20, 11, 14],
        [10, 27, 20],
        [ 9, 20, 11],
        [1

tensor([[14,  9, 19],
        [19, 11, 27],
        [21, 12,  9],
        [11, 12, 10],
        [10, 27,  9],
        [10, 30,  9],
        [13, 10, 23],
        [12,  9, 19],
        [10, 12,  9],
        [10, 22, 14],
        [ 9, 19, 11],
        [10, 28, 13],
        [21, 15,  9],
        [11, 15, 10],
        [27, 14,  9],
        [19, 11, 16],
        [16, 10, 23],
        [15,  9, 19],
        [19, 11, 17],
        [10, 22, 17],
        [ 9, 19, 11],
        [10, 28, 16],
        [21, 18,  9],
        [19, 11, 18],
        [27, 17,  9],
        [10, 37,  9],
        [19, 10, 23],
        [18,  9, 19],
        [20, 10, 19],
        [10, 22, 20],
        [ 9, 19, 11],
        [10, 28, 19],
        [11, 23, 14],
        [15,  9, 20],
        [10, 21, 12],
        [ 9, 20, 11],
        [12, 10, 27],
        [13, 10, 30],
        [20, 11, 13],
        [26, 12,  9],
        [11, 14, 10],
        [14, 10, 22],
        [13,  9, 20],
        [11, 14, 10],
        [10, 21, 15],
        [ 

## Maintain state

In [ ]:
class Model3(nn.Module):
    def __init__(self):
        super().__init__()
        self.i_h = nn.Embedding(nv,nh)
        self.h_h = nn.Linear(nh,nh)
        self.h_o = nn.Linear(nh,nv)
        self.bn = nn.BatchNorm1d(nh)
        self.h = torch.zeros(bs, nh).cuda()
        
    def forward(self, x):
        res = []
        h = self.h
        for i in range(x.shape[1]):
            h = h + self.i_h(x[:,i])
            h = F.relu(self.h_h(h))
            res.append(self.bn(h))
        self.h = h.detach()
        res = torch.stack(res, dim=1)
        res = self.h_o(res)
        return res

In [ ]:
learn = Learner(data, Model3(), metrics=accuracy)

In [ ]:
learn.fit_one_cycle(20, 3e-3)

## nn.RNN

In [ ]:
class Model4(nn.Module):
    def __init__(self):
        super().__init__()
        self.i_h = nn.Embedding(nv,nh)
        self.rnn = nn.RNN(nh,nh, batch_first=True)
        self.h_o = nn.Linear(nh,nv)
        self.bn = BatchNorm1dFlat(nh)
        self.h = torch.zeros(1, bs, nh).cuda()
        
    def forward(self, x):
        res,h = self.rnn(self.i_h(x), self.h)
        self.h = h.detach()
        return self.h_o(self.bn(res))

In [ ]:
learn = Learner(data, Model4(), metrics=accuracy)

In [ ]:
learn.fit_one_cycle(20, 3e-3)

## 2-layer GRU

In [ ]:
class Model5(nn.Module):
    def __init__(self):
        super().__init__()
        self.i_h = nn.Embedding(nv,nh)
        self.rnn = nn.GRU(nh, nh, 2, batch_first=True)
        self.h_o = nn.Linear(nh,nv)
        self.bn = BatchNorm1dFlat(nh)
        self.h = torch.zeros(2, bs, nh).cuda()
        
    def forward(self, x):
        res,h = self.rnn(self.i_h(x), self.h)
        self.h = h.detach()
        return self.h_o(self.bn(res))

In [ ]:
learn = Learner(data, Model5(), metrics=accuracy)

In [ ]:
learn.fit_one_cycle(10, 1e-2)

## fin